<a href="https://colab.research.google.com/github/MAEV-David/WindTurbine_Map/blob/main/Folium_Visualization_Examples_36WindTurbine_Map.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

> [教學](https://www.zhihu.com/question/33783546)

> [地理数据可视化 範例](https://nbviewer.jupyter.org/github/gaonanlee/Visualization-Practice/blob/master/Folium%20Visualization%20Examples.ipynb)

> [地理資料視覺化使用 Folium](https://blog.hanklu.tw/post/2019/folium/)

> [leaflet 结合 Echarts4 实现统计图(附源码下载)](https://www.programminghunter.com/article/7171480447/)




---
基本設定全教學

> [ipyleaflet: Interactive maps in the Jupyter notebook](https://ipyleaflet.readthedocs.io/en/latest/)

---

Folium 是基於 leaflet.js 視覺化地圖資料的套件，可以在 jupyter 直接顯示或是輸出成 HTML。



# 創建地圖
---

In [ ]:
import folium
import pandas as pd

In [ ]:
# define the world map
world_map = folium.Map()

# display world map
world_map

## 地圖樣式
---

Stamen Watercolor/Toner/Terrain/

* location=[lat,lng] 地圖中心的[緯度、經度]
* zoom_start 縮放的尺度
* tiles="OpenStreetMap" 地圖的樣式。

In [ ]:
# San Francisco latitude and longitude values
latitude = 37.77
longitude = -122.42

# Create map and display it
san_map = folium.Map(location=[latitude, longitude], 
                     zoom_start=12,
                     tiles='OpenStreetMap')

# Display the map of San Francisco
san_map

In [ ]:
# Change tiles of map
san_map = folium.Map(location=[latitude, longitude],
                     zoom_start=12, 
                     tiles='Stamen Terrain')
san_map

In [ ]:
# Change tiles of map
san_map = folium.Map(location=[latitude, longitude],
                     zoom_start=12, 
                     tiles='Stamen Toner')
san_map

## 匯出 HTML
---

In [ ]:
san_map.save("map.html")

## 範例資料_1 
---
https://www.zhihu.com/question/33783546

In [ ]:
# Read Dataset 
cdata = pd.read_csv('https://cocl.us/sanfran_crime_dataset')
cdata.head()

IncidntNum  ...            PdId
0   120058272  ...  12005827212120
1   120058272  ...  12005827212168
2   141059263  ...  14105926363010
3   160013662  ...  16001366271000
4   160002740  ...  16000274071000

[5 rows x 13 columns]

In [ ]:
# get the first 200 crimes in the cdata
limit = 200
data = cdata.iloc[0:limit, :]

# Instantiate a feature group for the incidents in the dataframe
incidents = folium.map.FeatureGroup()

# Loop through the 200 crimes and add each to the incidents feature group
for lat, lng, in zip(cdata.Y, data.X):
    incidents.add_child(
        folium.CircleMarker(
            [lat, lng],
            radius=7, # define how big you want the circle markers to be
            color='yellow',
            fill=True,
            fill_color='red',
            fill_opacity=0.4
        )
    )

# Add incidents to map
san_map = folium.Map(location=[latitude, longitude], zoom_start=12)
san_map.add_child(incidents)

In [ ]:
import json
import requests

url = 'https://cocl.us/sanfran_geojson'
san_geo = f'{url}'
san_map = folium.Map(location=[37.77, -122.4], zoom_start=12)
folium.GeoJson(
    san_geo,
    style_function=lambda feature: {
        'fillColor': '#ffff00',
        'color': 'black',
        'weight': 2,
        'dashArray': '5, 5'
    }
).add_to(san_map)

#display map
san_map

In [ ]:
# Count crime numbers in each neighborhood
disdata = pd.DataFrame(cdata['PdDistrict'].value_counts())
disdata.reset_index(inplace=True)
disdata.rename(columns={'index':'Neighborhood','PdDistrict':'Count'},inplace=True)
disdata

Neighborhood  Count
0     SOUTHERN  28445
1     NORTHERN  20100
2      MISSION  19503
3      CENTRAL  17666
4      BAYVIEW  14303
5    INGLESIDE  11594
6      TARAVAL  11325
7   TENDERLOIN   9942
8     RICHMOND   8922
9         PARK   8699

In [ ]:
san_map = folium.Map(location=[37.77, -122.4], zoom_start=12)

# Create Choropleth map
folium.Choropleth(
    geo_data=san_geo,
    data=disdata,
    columns=['Neighborhood','Count'],
    key_on='feature.properties.DISTRICT',
    #fill_color='red',
    fill_color='YlOrRd',
    fill_opacity=0.7,
    line_opacity=0.2,
    highlight=True,
    legend_name='Crime Counts in San Francisco'
).add_to(san_map)

san_map

In [ ]:
san_map = folium.Map(location=[37.77, -122.4], zoom_start=12)

# Create Choropleth map
folium.Choropleth(
    geo_data=san_geo,
    data=disdata,
    columns=['Neighborhood','Count'],
    key_on='feature.properties.DISTRICT',
    #fill_color='red',
    fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=0.2,
    highlight=True,
    legend_name='Crime Counts in San Francisco'
).add_to(san_map)

san_map

In [ ]:
from folium.plugins import HeatMap

# let's start again with a clean copy of the map of San Francisco
san_map = folium.Map(location = [latitude, longitude], zoom_start = 12)

# Convert data format
heatdata = data[['Y','X']].values.tolist()

# add incidents to map
HeatMap(heatdata).add_to(san_map)

san_map

## 範例資料_2 
---
https://blog.hanklu.tw/post/2019/folium/

以台北市 Youbike 的 GPS 資料為例，在地圖上點出各個站點。


> **範例資料**

[**Youbike 站點**](https://blog.hanklu.tw/static/folium/station.json)

* tot: 站點的樁數
* sna: 站點的名稱
* lat: 緯度
* lng: 經度

[**臺北市區界**](https://blog.hanklu.tw/static/folium/TPgeo.json)
* 各行政區 GeoJson


# 資料點
---
將資料點加入地圖

> **Circle**

```
folium.Circle(
    radius=radius,
    location=[point.position.lat, point.position.lng],
    popup=popup,
    fill_color=color,
    fill_opacity=1,
    color="#555",
    weight=1
).add_to(san_map)
```

* radius: 圓圈的大小(公尺)
* location: [緯度, 經度]
* popup: 滑鼠點擊時跳出來的訊息
* stroke: 是否顯示框線(Bool)
* color: 框線顏色
* weight: 框線粗細
* opacity: 框線透明度
* fill: 是否填入顏色 (Bool)
* fill_color: 圓圈填入的顏色
* fill_opacity: 填入顏色的透明度

In [ ]:
# 讀取資料
stations = json.load(open("station.json","r"))

# 創建地圖
m = folium.Map(location=[25.0431, 121.539723],
               zoom_start=13,
               tiles="cartodbpositron")

# 將資料點加到地圖上
for station in stations:
    folium.Circle(
        radius=50,
        location=[station["lat"], station["lng"]],
        popup="{} \n {}".format(station["sna"],station["tot"]),
        color="#555",
        weight=1,
        fill_color="#FFE082",
        fill_opacity=1,

    ).add_to(m)
m

## ICON
---

[Font awesome](https://fontawesome.com/v5.15/icons?d=gallery&p=2)

> **Marker**

```
folium.Marker(
    location=[25.0431, 121.539723],
    icon=folium.Icon(color="red",icon_color="blue",icon='fa-truck', prefix='fa')
).add_to(m)
```

* color
* icon_color
* icon: Font awesome
* popup: 滑鼠點擊時跳出來的訊息
* prefix: icon source 的 prefix

In [ ]:
folium.Marker(
    location=[25.0431, 121.539723],
    icon=folium.Icon(color="red",icon='fa-truck', prefix='fa')).add_to(m)

folium.Marker(
    location=[25.0431, 121.569723],
        popup='Cloud',
    icon=folium.Icon(icon='cloud')
).add_to(m)

m

# 線段
---

> **PolyLine**

```
folium.PolyLine(
    locations,
    color="blue",
    weight=4,
    opacity=0.5
).add_to(m)
```

* locations: list of [lat,lng]
* popup: 滑鼠點擊時跳出來的訊息
* tooltip: 滑鼠移到上方時顯示訊息





In [ ]:
path = [(s["lat"],s["lng"]) for s in stations[10:20]] # 選 10 個站連線

folium.PolyLine(
    path,
    color="blue",
    weight=4,
    opacity=0.5,
    smooth_factor=5.
).add_to(m)
m

# 區域
---
地理區域資料

1. [GeoJson.io](https://geojson.io/#map=2/20.0/0.0) 圈出想要的區域
2. 政府開放資料，如鄉鎮界線、縣市界線

## GeoJson
---

> **GeoJson**


```
folium.GeoJson(
    region,
    name='geojson',
    style_function=lambda x : {"fillColor":colorscale(random.randrange(0,10)),"fillOpacity":1}
).add_to(m)
```

* data: GeoJson 格式的資料
* style_function: 回傳包含樣式的 dict
    * stroke
    * color
    * dashArray:
    * weight
    * fillColor
    * FillOpacity



In [ ]:
import branca
import random
import json

colorscale = branca.colormap.linear.YlOrRd_09.scale(0, 20) # color scale

m = folium.Map(location=[24.3970610305272, 120.365602883822],
               width='100%',
               height='100%',
               zoom_start=10,
               tiles="OpenStreetMap")


for region in json.load(open("36區塊潛力場址TWD97座標點位資料_lon_lat.json")):
    folium.GeoJson(
        region,
        name='geojson',
        style_function=lambda feature : {
            "fillColor":colorscale(random.randrange(0,20)),
            "fillOpacity":.5,
            "stroke" : False}
    ).add_to(m)
m


NameError: ignored

### 實例：離岸風電潛力風場

In [ ]:
import folium
# from folium.features import GeoJsonPopup, GeoJsonTooltip
import branca
import random
import json
import pandas as pd
import numpy as np
import webbrowser

## 匯入資料
df = pd.read_csv('36區塊潛力場址TWD97座標點位資料_lon_lat_2.csv')

## 地圖創建
colorscale = branca.colormap.linear.YlOrRd_09.scale(0, 20) # color scale

m = folium.Map(location=[24.3970610305272, 120.365602883822],
               width='100%',
               height='100%',
               zoom_start=10,
               tiles="OpenStreetMap",
               attr='Copyright: © Chen, Chi-Wei | Map data: © <a href="http://www.openstreetmap.org/copyright">OpenStreetMap</a>, <a href="http://viewfinderpanoramas.org">SRTM</a> | Map style: © <a href="https://opentopomap.org">OpenTopoMap</a> (<a href="https://creativecommons.org/licenses/by-sa/3.0/">CC-BY-SA</a>)')

def folium_Polygon(array, row_title):
    
    Title = '''
            <p>
            <h5>City：{} </h5>
            <h5>Area：{} </h5>
            <h5>No：{}</h5>
            </p>
            '''.format(df.iloc[row_title][1], df.iloc[row_title][2], df.iloc[row_title][3] )
    # iframe = folium.IFrame(Title)
    popup = folium.Popup(Title , max_width=120)
    # tooltip = "Click Here For More Info"
    tooltip = Title

    folium.Polygon(array,
                   color = 'red',
                   weight = 1, 
                   fill = True, 
                   fill_color = 'red', 
                   fill_opacity = 0.5,
                   popup = popup,
                   tooltip = tooltip
    ).add_to(m)

## 將資料加入地圖中
# len(df.index)
# print(df.iloc[0, 3])
# print(df.isna().iloc[0, 3])
for row in range(len(df.index)):
    counts = 1
    if df.isna().iloc[row, 3] == True:
        continue
    elif df.isna().iloc[row, 3] == False:
        # 風場起始點資訊 
        row_title = row
        array = [[df.iloc[row, 8], df.iloc[row, 7]]]
        # array = [[]]
        while df.isna().iloc[row+counts, 3] == True:
            if (row+counts < len(df.index)-1):
                array = [[df.iloc[row+counts, 8], df.iloc[row+counts, 7]]] + array
                counts += 1
            else:
                array = [[df.iloc[row+counts, 8], df.iloc[row+counts, 7]]] + array
                break
        folium_Polygon(array, row_title)
        print('------------------', df.iloc[row, 3])
    
    # print(array)

## 迷你地圖
from folium.plugins import MiniMap
minimap = MiniMap(toggle_display=True,          # 摺疊(收起來)
                  # width=200, height=200,      # 尺寸
                  zoom_level_offset=-4,         # 縮放比例
                  tile_layer='OpenStreetMap')   # 換底圖
m.add_child(minimap)

## Layers and Tiles in Folium
from branca.element import Figure
fig = Figure(width=1000, height=700)
fig.add_child(m)
folium.TileLayer('Stamen Terrain').add_to(m)
folium.TileLayer('Stamen Toner').add_to(m)
folium.TileLayer('Stamen Water Color').add_to(m)
folium.TileLayer('cartodbpositron').add_to(m)
folium.TileLayer('cartodbdark_matter').add_to(m)
# folium.LayerControl().add_to(m)

## 隱藏icon
from folium import FeatureGroup
feature_group = FeatureGroup(name="Some icons")
feature_group.add_to(m)
folium.LayerControl(collapsed=True).add_to(m)

## Measurementcontrol 量測地圖功能
from folium.plugins import MeasureControl
m.add_child(MeasureControl())#量測地圖功能加入

## 加入圖片（例：指北針）
from folium.plugins import FloatImage
url = ("https://raw.githubusercontent.com/SECOORA/static_assets/master/maps/img/rose.png")
FloatImage(url, bottom=1.5, left=0).add_to(m)

## Fullscreen
from folium import plugins
plugins.Fullscreen(
    position="topright",
    title="Expand me",
    title_cancel="Exit me",
    force_separate_button=True,
).add_to(m)

## 經緯度
from folium.plugins import MousePosition
MousePosition(position="bottomleft").add_to(m)

## 畫圖工具
from folium.plugins import Draw
draw = Draw(export=False)
draw.add_to(m)

'''
## 搜尋
from folium.plugins import Search
citysearch = Search(
    layer=citygeo,
    geom_type="Point",
    placeholder="Search for a US City",
    collapsed=True,
    search_label="nameascii",
).add_to(m)
'''

## Save
m.save("36區塊潛力場址.html")
webbrowser.open("36區塊潛力場址.html")
m

------------------ 1
------------------ 2
------------------ 3
------------------ 4
------------------ 5
------------------ 6
------------------ 7
------------------ 7-2
------------------ 8
------------------ 9
------------------ 10
------------------ 11
------------------ 12
------------------ 13
------------------ 14
------------------ 15
------------------ 16
------------------ 17
------------------ 18
------------------ 19
------------------ 20
------------------ 21
------------------ 22
------------------ 23
------------------ 24
------------------ 25
------------------ 26
------------------ 27
------------------ 28
------------------ 29
------------------ 30
------------------ 31
------------------ 32
------------------ 33
------------------ 34
------------------ 35
------------------ 36
------------------ 36-2


### 加入衛星資料

> [VideoOverlayLayer.ipynb](https://nbviewer.jupyter.org/github/python-visualization/folium/blob/master/examples/VideoOverlayLayer.ipynb)

In [ ]:
import folium

m = folium.Map(location=[22.5, -115], zoom_start=4)

video = folium.raster_layers.VideoOverlay(
    video_url="https://www.mapbox.com/bites/00188/patricia_nasa.webm",
    bounds=[[32, -130], [13, -100]],
    opacity=0.65,
    attr="Video from patricia_nasa",
    autoplay=True,
    loop=False,
)

video.add_to(m)

m

>  [WMS_and_WMTS.ipynb](https://nbviewer.jupyter.org/github/python-visualization/folium/blob/master/examples/WMS_and_WMTS.ipynb)

In [ ]:
import folium


m = folium.Map(location=[41, -70], zoom_start=5, tiles=None)


folium.raster_layers.TileLayer(
    tiles="http://{s}.google.com/vt/lyrs=s&x={x}&y={y}&z={z}",
    attr="google",
    name="google maps",
    max_zoom=20,
    subdomains=["mt0", "mt1", "mt2", "mt3"],
    overlay=False,
    control=True,
).add_to(m)

folium.raster_layers.TileLayer(
    tiles="http://{s}.google.com/vt/lyrs=m&x={x}&y={y}&z={z}",
    attr="google",
    name="google street view",
    max_zoom=20,
    subdomains=["mt0", "mt1", "mt2", "mt3"],
    overlay=False,
    control=True,
).add_to(m)


folium.raster_layers.WmsTileLayer(
    url="http://mesonet.agron.iastate.edu/cgi-bin/wms/nexrad/n0r.cgi",
    name="test",
    fmt="image/png",
    layers="nexrad-n0r-900913",
    attr=u"Weather data © 2012 IEM Nexrad",
    transparent=True,
    overlay=True,
    control=True,
).add_to(m)

folium.LayerControl().add_to(m)

m

> [這可能是 Python 裡最強的繪製地圖神器](https://www.gushiciku.cn/pl/g4Iz/zh-tw)


In [ ]:
import folium
 
m = folium.Map(location=[39.917834, 116.397036], zoom_start=13, width='100%',height='100%', zoom_control='False',
 
               tiles='http://webrd02.is.autonavi.com/appmaptile?lang=zh_cn&size=1&scale=1&style=8&x={x}&y={y}&z={z}&ltype=6',attr='AutoNavi')
 
 

tooltip ='請點選我檢視該點資訊'
 
folium.Marker([39.937282,116.403187], popup='南鑼鼓巷',tooltip=tooltip).add_to(m)
 
folium.Marker([39.917834,116.397036], popup='故宮',tooltip=tooltip).add_to(m)
 
folium.Marker([39.928614,116.391746], popup='北海公園', tooltip=tooltip, icon=folium.Icon(color='red')).add_to(m)
 
folium.Marker([39.942143,116.382590], popup='後海公園', tooltip=tooltip, icon=folium.Icon(color='green', prefix='fa', icon='taxi')).add_to(m)
 
folium.Marker([39.917834,116.397036], popup='故宮').add_to(m)
 
folium.Marker([39.928614,116.391746], popup='北海公園').add_to(m)
 
folium.Marker([39.937282,116.403187], popup='南鑼鼓巷').add_to(m)
 
folium.Marker([39.942143,116.382590], popup='後海公園').add_to(m)
 
 
folium.Polygon([
 
    [39.917834,116.397036],
 
    [39.928614,116.391746],
 
    [39.942143,116.382590],
 
    [39.937282,116.403187],
 
],color='blue', weight=2, fill=True, fill_color='blue', fill_opacity=0.3).add_to(m)
m

In [ ]:
list1 = json.load(open("36區塊潛力場址TWD97座標點位資料.json", "r"))

print(list1)

for _ in list1:
    list2=list(_.values())
    print(list2)

### TWD97座標轉換
---

[ 利用Python撰寫經緯度 / TWD97坐標轉換](http://fyyang.blogspot.com/2012/09/python-twd97.html)

In [ ]:
!pip install pyproj

     |████████████████████████████████| 6.6MB 8.4MB/s 


In [ ]:
import pyproj

TWD97 = pyproj.Proj(init='epsg:3826') #定義TWD97坐標系
WGS84 = pyproj.Proj(init='epsg:4326') #定義WGS84坐標系


lon,lat = TWD97(120.316135253,22.7286904948)
#將WGS84經緯度轉成TWD97坐標
print(lon,lat)

lon,lat = pyproj.transform(TWD97, WGS84,179754.960,2514402.715)
#將TWD97坐標轉成WGS84經緯度
print(lon,lat)

179754.96003631147 2514402.714995935
120.31613525264632 22.728690494835188


/usr/local/lib/python3.7/dist-packages/pyproj/crs/crs.py:68: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/usr/local/lib/python3.7/dist-packages/pyproj/crs/crs.py:306: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/usr/local/lib/python3.7/dist-packages/pyproj/crs/crs.py:68: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axi

In [ ]:
df = pd.read_csv('36區塊潛力場址TWD97座標點位資料_lon_lat.csv')
df.head()
for row in range(0,230):
    lon, lat = pyproj.transform(TWD97, WGS84, df.iloc[row, 5], df.iloc[row, 6])
    df.iloc[row, 7], df.iloc[row, 8] = lon, lat
    #將TWD97坐標轉成WGS84經緯度
df.head()
df.to_csv("36區塊潛力場址TWD97座標點位資料_lon_lat.csv")

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  """
